# Notebook Objective and Setup

In BGG07 we build several large datasets, notably:

* Real Ratings Dictionaries and Longform(melted) Dataframes in both unscaled and scaled versions
* Synthetic Ratings Dictionaries and Longform Dataframes in both unscaled and scaled versions, for 100, 250 and 500
* User Means lookup dictionary

These files are used in the Collaborative Filter (BGG08)

## Notebook Preparation

### Package Imports

In [1]:
import pandas as pd
import numpy as np
import requests
import regex as re
import time
import os
import gc
import json
from statistics import mean
import copy

# ignore warnings (gets rid of Pandas copy warnings)
import warnings
warnings.filterwarnings('ignore')
pd.options.display.max_columns = None

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', 30)

### Notebook Functions

In [2]:
def get_user(user_items, user, game_ids, scaled=True):
    '''
    Takes in a sparse matrix of users and items, a specific user to retrieve, and a list of game_ids
    Get the mean for the user
    Builds a list of user's rated items and subtracts user mean from all ratings
    Builds a corresponding list of game ids for the rated games
    Gets intersection of user's rated ids with the overall game_ids
    Stores user game_id:rating in user ratings dictionary 
    Returns the user dictionary
    
    Inputs: 
    user_matrix: sparse matrix of users and game ratings
    user: user to retrieve
    game_ids: all possible game_ids in matrix
    scaled: default true, is whether to remove user's mean from their ratings
    
    Outputs:
    overall_user: user entry with user's game ratings
    '''
    
    # get the mean rating for that user
    user_mean = user_items.mean()
    
    if scaled:
    # normalize the ratings for that user by subtracting their mean from all ratings, store in list
        game_ratings_normed =  list(user_items - user_mean)
    
    else:
        game_ratings_normed = list(user_items)
    
    # Get a list of all of the game IDs that the user rated (meaning are not NaN)
    users_game_ids = list(user_items.index)
    
    user_ratings = {}
    
    for key, value in zip(users_game_ids, game_ratings_normed):
        user_ratings[key] = value
    
    game_ids_set = set(game_ids).intersection(set(users_game_ids))
    
    # make a dictionary to store the intersected ratings
    set_dictionary = {}
    
    # for each matching key, value in game_ids and game_ratings for the user
    for item in game_ids_set:
        set_dictionary[item] = user_ratings[item]

    # store the user's ratings
    overall_user = set_dictionary
    
    return overall_user

In [3]:
def make_user_dictionaries(path_item, scaled=True):
    ''' Loads a user ratings matrix, cleans, and returns as ratings dictionary
    
    Inputs: path
    Scaled: default true, passes to get_user
    
    Outputs: ratings dictionary for this file
    '''

    temp_dictionary = {}
    
    path = 'data_cleaned_new_scraper/ratings_matrix_cleaned_'+path_item+'.pkl'
    user_matrix = pd.read_pickle(path)
    user_matrix = user_matrix.T
    user_matrix.index = user_matrix.index.astype('int32')
    user_matrix.shape
    
    for user in user_matrix.columns:
           
        print("Starting user "+user)
        
        user_items = user_matrix[user].dropna(axis=0)
           
        # copy the current user dictionary to the synthetic ratings storage dictionary
        temp_dictionary[user] = get_user(user_items, user, game_ids, scaled)
    
    return temp_dictionary

In [4]:
def make_long_df(path, scaled=True):
    ''' Melts a user ratings dictionary into a longform dataframe
    
    Inputs: path, passes to make_user_dictionaries
    scaled: default true, passes to make_user_dictionaries then get_user
    '''
    # call for dictionary
    temp_dictionary = make_user_dictionaries(path, scaled)
    
    # melt dictionary into longform DF
    real_user_ratings = pd.DataFrame.from_dict(temp_dictionary).T
    real_user_ratings.reset_index(inplace=True)
    real_user_ratings.rename(columns={'index':'UserID'}, inplace=True)
    real_user_ratings_long = real_user_ratings.melt(id_vars='UserID', var_name='BGGId', value_name='Rating').dropna()
    real_user_ratings_long.sort_values('UserID', inplace=True)
    real_user_ratings_long.reset_index(drop=True, inplace=True)

    del real_user_ratings
    gc.collect()
    
    return temp_dictionary, real_user_ratings_long

In [5]:
# load and make game id list
games = pd.read_pickle('data_cleaned/games.pkl')

game_ids = list(games['BGGId'])

# Build Real Ratings Dictionaries

Build the various data sets

## Unscaled Ratings

In [6]:
path = 'data_cleaned/ratings_matrix_cleaned_01.pkl'
user_matrix = pd.read_pickle(path)
user_matrix = user_matrix.T
user_matrix.index = user_matrix.index.astype('int32')
user_matrix.shape

(21000, 15070)

In [ ]:
temp_dictionary01, real_user_ratings_long_01 = make_long_df('01', scaled=False)
temp_dictionary02, real_user_ratings_long_02 = make_long_df('02', scaled=False)
temp_dictionary03, real_user_ratings_long_03 = make_long_df('03', scaled=False)
temp_dictionary04, real_user_ratings_long_04 = make_long_df('04', scaled=False)
temp_dictionary05, real_user_ratings_long_05 = make_long_df('05', scaled=False)
temp_dictionary06, real_user_ratings_long_06 = make_long_df('06', scaled=False)

### Lookup Dictionary

In [9]:
real_user_ratings_dictionary_unscaled = {}
real_user_ratings_dictionary_unscaled.update(temp_dictionary01)
real_user_ratings_dictionary_unscaled.update(temp_dictionary02)
real_user_ratings_dictionary_unscaled.update(temp_dictionary03)
real_user_ratings_dictionary_unscaled.update(temp_dictionary04)
real_user_ratings_dictionary_unscaled.update(temp_dictionary05)
real_user_ratings_dictionary_unscaled.update(temp_dictionary06)

In [10]:
len(real_user_ratings_dictionary_unscaled)

117263

In [11]:
with open('real_ratings/real_user_ratings_dictionary_unscaled.json', 'w') as convert_file:
     convert_file.write(json.dumps(real_user_ratings_dictionary_unscaled))

In [12]:
del real_user_ratings_dictionary_unscaled
gc.collect()

21

### Longform DF

In [13]:
real_user_ratings_long_unscaled = pd.concat([real_user_ratings_long_01, real_user_ratings_long_02, real_user_ratings_long_03, real_user_ratings_long_04, real_user_ratings_long_05, real_user_ratings_long_06], ignore_index=True)

In [14]:
real_user_ratings_long_unscaled.shape

(11526767, 3)

In [15]:
real_user_ratings_long_unscaled.to_pickle('real_ratings/real_user_ratings_long_unscaled.pkl')

In [16]:
del real_user_ratings_long_unscaled
gc.collect()

84

## Scaled Ratings

In [17]:
temp_dictionary01, real_user_ratings_long_01 = make_long_df('01', scaled=True)
temp_dictionary02, real_user_ratings_long_02 = make_long_df('02', scaled=True)
temp_dictionary03, real_user_ratings_long_03 = make_long_df('03', scaled=True)
temp_dictionary04, real_user_ratings_long_04 = make_long_df('04', scaled=True)
temp_dictionary05, real_user_ratings_long_05 = make_long_df('05', scaled=True)
temp_dictionary06, real_user_ratings_long_06 = make_long_df('06', scaled=True)

Starting user -Johnny-
Starting user -LucaS-
Starting user -Morphling-
Starting user -PEDROPABLO-
Starting user -mIDE-
Starting user -snarf-
Starting user -toni-
Starting user -xXx-
Starting user ...Hammer
Starting user .JcK.
Starting user 0 1 1 2 3 5 8
Starting user 00Bogey
Starting user 00daniel00
Starting user 00vito
Starting user 01151125
Starting user 015599m
Starting user 01josepe
Starting user 01lwilliams
Starting user 020907
Starting user 0447603
Starting user 07734
Starting user 0815Spieler
Starting user 0CanuckEh
Starting user 0Kage
Starting user 0Shea0
Starting user 0b1_Ita
Starting user 0handle
Starting user 0hoHj
Starting user 0kecske0
Starting user 0lexandr
Starting user 0lukasz0
Starting user 0minus
Starting user 0rOmO0
Starting user 0rlo
Starting user 0stuart0
Starting user 0time
Starting user 0v3rl0r17
Starting user 0xA8E
Starting user 1 Family Meeple
Starting user 1 Lucky Texan
Starting user 1 Oak
Starting user 1 Up
Starting user 1 of 5
Starting user 1000days
Starting

Starting user 7of9
Starting user 7ofAnn
Starting user 7quark
Starting user 7rich7
Starting user 7thDRXN
Starting user 7thsanctum
Starting user 7times7is49
Starting user 7umaca
Starting user 80110X
Starting user 807johnilkka
Starting user 80_sound
Starting user 80sGirl
Starting user 80sbgamer
Starting user 810gamingsociety
Starting user 81blixa
Starting user 839543050
Starting user 84905
Starting user 84pandora
Starting user 84tigers
Starting user 85_falk
Starting user 85bears
Starting user 86Oscargarnav
Starting user 88136560
Starting user 8823
Starting user 88FosteR
Starting user 89170
Starting user 8BALL1972
Starting user 8BITFISH
Starting user 8Reaper7
Starting user 8bit
Starting user 8bit Geezer
Starting user 8bitdad
Starting user 8bitmage
Starting user 8eagle
Starting user 8odoros
Starting user 8one6
Starting user 8orbit
Starting user 8thDay
Starting user 8th_Angel
Starting user 8tlas
Starting user 90krisz90
Starting user 90stones
Starting user 9137enrico
Starting user 93MadeGames

Starting user Abby
Starting user Abby312
Starting user Abdul
Starting user Abdurrahim Armagan
Starting user Abe227
Starting user AbeLincoln
Starting user Abeatron
Starting user Abekongen
Starting user Aberdeen1977
Starting user Aberdonian
Starting user Aberrix
Starting user Abex17
Starting user AbgalAzag
Starting user Abhilash
Starting user Abia
Starting user Abiezer Coppe
Starting user Abigail
Starting user AbigailAKessler
Starting user Abilius_XXI
Starting user Abinrml
Starting user Abisteen
Starting user Abiteacher
Starting user AbleCompany
Starting user AbleTableGaming
Starting user AbnRgr
Starting user Abner Nirtzman
Starting user Abner1
Starting user AboDani
Starting user Abom1nation
Starting user Abomut
Starting user AbovetheLawson
Starting user Abracasmakya
Starting user Abraham_linc007
Starting user Abraham_tellez
Starting user Abram Tertz
Starting user AbraxiS
Starting user Abraxox
Starting user Abraxx
Starting user Abreu
Starting user Abruk
Starting user Abry545
Starting use

Starting user Aerin41
Starting user Aeris7
Starting user Aerius1979
Starting user Aerjen
Starting user Aermord
Starting user AeroGirl
Starting user AeroHudson
Starting user Aerogator
Starting user Aeron13
Starting user Aerothorn
Starting user Aerox
Starting user Aertirath
Starting user Aescholus
Starting user Aescwicca
Starting user Aesdel
Starting user Aeshe
Starting user Aeszett
Starting user Aethariel
Starting user Aethelaf
Starting user Aethelwulf
Starting user Aether42
Starting user AetherStrider
Starting user AetherTower
Starting user Aetherkhaos
Starting user Aetheros
Starting user Aetos18
Starting user Aevey
Starting user Aevum Decessus
Starting user AfarOca
Starting user Afarle73
Starting user Afem
Starting user Affe1982
Starting user Affenberg
Starting user Affensohn
Starting user Affinity123
Starting user Afflicter
Starting user Affy
Starting user Affynity
Starting user Afirm8
Starting user Afkamm
Starting user Afon
Starting user Afortu80
Starting user Afram64
Starting user 

Starting user Alan Kwan
Starting user Alan Paull
Starting user Alan R
Starting user Alan Saunders
Starting user Alan Steinberg
Starting user Alan Stern
Starting user Alan250
Starting user AlanCaselli
Starting user AlanDAmico81
Starting user AlanMorillo
Starting user AlanPoint45kg
Starting user AlanScott74
Starting user AlanSpence81
Starting user Alan_De_Smet
Starting user Alan_E
Starting user Alanako26
Starting user Alandor
Starting user Alannamairead
Starting user Alansmithee007
Starting user Alarian
Starting user Alarka
Starting user Alarya
Starting user Alaryon
Starting user AlasDemigod
Starting user Alasdair333
Starting user Alashar
Starting user Alaskaben
Starting user Alaskanhobbit
Starting user Alaskowski
Starting user Alaurie27
Starting user Alavaster
Starting user Alaxiska
Starting user Alazabba
Starting user Alb85
Starting user Albarc
Starting user Albatraous
Starting user Albatrocity
Starting user Albatros28215
Starting user Albe Pavo
Starting user AlbeitarD
Starting user Al

...

Starting user wnverhoef
Starting user woPLrdAY
Starting user wobbel
Starting user wobbly
Starting user wobblysquare
Starting user wobo
Starting user woda
Starting user wodkers
Starting user wodlf
Starting user wodzmuerte
Starting user woeful
Starting user woega
Starting user woelfman
Starting user woerlinsel
Starting user woetly
Starting user wogget
Starting user woggoli
Starting user wogns0630
Starting user wogy
Starting user wohali
Starting user wohoel
Starting user wohomerhoo
Starting user woiny
Starting user woj_settlers
Starting user wojciechk
Starting user wojkap
Starting user wojtast
Starting user wojtaszek23
Starting user wojtigup
Starting user wojtkielewicz67
Starting user wojtolino
Starting user wojtyk
Starting user wolaberry
Starting user woland57
Starting user woldview
Starting user woldwarrior
Starting user wolf08
Starting user wolf555
Starting user wolf642
Starting user wolfboy193
Starting user wolfchild59
Starting user wolfden76
Starting user wolfejo
Starting user wolfen

Starting user xabelmagno
Starting user xabieret
Starting user xacal1989
Starting user xacalsk8
Starting user xachan
Starting user xaddew
Starting user xadrastosx
Starting user xagentman
Starting user xalakis
Starting user xaldin
Starting user xalons
Starting user xamQC
Starting user xamax
Starting user xamboto
Starting user xamn
Starting user xamsedel
Starting user xanadu1215
Starting user xanalor
Starting user xander1960
Starting user xandercm
Starting user xanderlynn
Starting user xanderp
Starting user xanderstang
Starting user xandolino
Starting user xandre_cr
Starting user xandrellas
Starting user xandria
Starting user xandros_gr
Starting user xandryyte
Starting user xango
Starting user xann
Starting user xanofere
Starting user xanshin
Starting user xant_valley
Starting user xantheji
Starting user xanthie
Starting user xanthipos
Starting user xanthrax
Starting user xantio
Starting user xantm70
Starting user xantor1
Starting user xanwan
Starting user xaosist
Starting user xaponeis
S

Starting user yendi57
Starting user yendorii
Starting user yenkin2001
Starting user yenkoberli
Starting user yennifer
Starting user yennijb
Starting user yentzernathan
Starting user yeoj
Starting user yerbaceo
Starting user yesbryn
Starting user yesfantina
Starting user yeshuasoldier
Starting user yesman68
Starting user yesnid
Starting user yeti_is_coming
Starting user yetibamsen
Starting user yetik
Starting user yetikeeper
Starting user yetirydr
Starting user yetisRfury
Starting user yezimy
Starting user yffip
Starting user yggdrasyl
Starting user yggsdrasil23
Starting user ygoduelistharry
Starting user ygtyrt
Starting user yha_diks
Starting user yhelfman
Starting user yhwhymlk
Starting user yi92
Starting user yichof
Starting user yichu1123
Starting user yid0
Starting user yifeidu
Starting user yildun
Starting user yin yang
Starting user yingling
Starting user yinling2020
Starting user yiorgolas
Starting user yip1
Starting user yipiyip
Starting user yisseung
Starting user yisun518
Sta

Starting user zavesky
Starting user zavijahbeta
Starting user zavulon
Starting user zaxa
Starting user zazasLT
Starting user zazenpanda
Starting user zazery
Starting user zb1035
Starting user zbajszek
Starting user zberkoff
Starting user zbizek1
Starting user zboat
Starting user zbone
Starting user zbruss
Starting user zbunc17
Starting user zbv500
Starting user zbyshekh
Starting user zc1993
Starting user zcapr17
Starting user zcelloman
Starting user zchillman
Starting user zd2046
Starting user zdalekacelny
Starting user zdenda
Starting user zdepthcharge
Starting user zdkat
Starting user zdpierson
Starting user zdtorok
Starting user ze_dutch_kiwi
Starting user ze_stom
Starting user zeaklous
Starting user zeaksevers
Starting user zeal
Starting user zealisee
Starting user zeamadevarza
Starting user zeanarchy
Starting user zebani200
Starting user zebedeemcdougal
Starting user zebinomancer
Starting user zebius
Starting user zebracat
Starting user zebragod
Starting user zebrastuhl
Starting u

Starting user zulafangchu
Starting user zulcus
Starting user zulupt
Starting user zuluragnok
Starting user zumba
Starting user zumby65
Starting user zumikon
Starting user zumo
Starting user zunnesteke
Starting user zupertails
Starting user zurfarosa
Starting user zurn
Starting user zurupeto
Starting user zurzu
Starting user zusje17
Starting user zusterdoor
Starting user zutcorp
Starting user zutman888
Starting user zuto
Starting user zuviel
Starting user zuzubun
Starting user zuzusdad
Starting user zwalex
Starting user zwarbo
Starting user zwbsch
Starting user zweifel
Starting user zweigefuhle
Starting user zwinky
Starting user zwinx
Starting user zwobot
Starting user zwodder
Starting user zwyagel
Starting user zx80
Starting user zxcv411
Starting user zxcvbn2
Starting user zxlime
Starting user zxlitening45
Starting user zyater
Starting user zygfryd78
Starting user zyklonc
Starting user zylan
Starting user zymil
Starting user zyph
Starting user zyquareo
Starting user zyrain
Starting use

### Lookup Dictionary

In [18]:
real_user_ratings_dictionary_scaled = {}
real_user_ratings_dictionary_scaled.update(temp_dictionary01)
real_user_ratings_dictionary_scaled.update(temp_dictionary02)
real_user_ratings_dictionary_scaled.update(temp_dictionary03)
real_user_ratings_dictionary_scaled.update(temp_dictionary04)
real_user_ratings_dictionary_scaled.update(temp_dictionary05)
real_user_ratings_dictionary_scaled.update(temp_dictionary06)

In [19]:
len(real_user_ratings_dictionary_scaled)

117263

In [20]:
with open('real_ratings/real_user_ratings_dictionary_scaled.json', 'w') as convert_file:
     convert_file.write(json.dumps(real_user_ratings_dictionary_scaled))

In [21]:
del real_user_ratings_dictionary_scaled
gc.collect()

21

### Longform DF

In [22]:
real_user_ratings_long_scaled = pd.concat([real_user_ratings_long_01, real_user_ratings_long_02, real_user_ratings_long_03, real_user_ratings_long_04, real_user_ratings_long_05, real_user_ratings_long_06], ignore_index=True)

In [23]:
real_user_ratings_long_scaled.shape

(11526767, 3)

In [24]:
real_user_ratings_long_scaled.to_pickle('real_ratings/real_user_ratings_long_scaled.pkl')

In [25]:
del real_user_ratings_long_scaled
gc.collect()

84

# Build Synthetic Ratings Dictionaries

## Scaled Ratings

### Lookup Dictionary

In [6]:
def make_lookup(appendation):
    # Opening JSON file
    with open('synthetic_ratings_new_scraper/users_dump_syntheticratings01'+appendation+'.json') as json_file:
        users_dump_syntheticratings01 = json.load(json_file)
    with open('synthetic_ratings_new_scraper/users_dump_syntheticratings02'+appendation+'.json') as json_file:
        users_dump_syntheticratings02 = json.load(json_file)
    with open('synthetic_ratings_new_scraper/users_dump_syntheticratings03'+appendation+'.json') as json_file:
        users_dump_syntheticratings03 = json.load(json_file)
    with open('synthetic_ratings_new_scraper/users_dump_syntheticratings04'+appendation+'.json') as json_file:
        users_dump_syntheticratings04 = json.load(json_file)
    with open('synthetic_ratings_new_scraper/users_dump_syntheticratings05'+appendation+'.json') as json_file:
        users_dump_syntheticratings05 = json.load(json_file)
    with open('synthetic_ratings_new_scraper/users_dump_syntheticratings06'+appendation+'.json') as json_file:
        users_dump_syntheticratings06 = json.load(json_file)
                                                  
    synth_user_ratings_dictionary_scaled = {}
    synth_user_ratings_dictionary_scaled.update(users_dump_syntheticratings01)
    synth_user_ratings_dictionary_scaled.update(users_dump_syntheticratings02)
    synth_user_ratings_dictionary_scaled.update(users_dump_syntheticratings03)
    synth_user_ratings_dictionary_scaled.update(users_dump_syntheticratings04)
    synth_user_ratings_dictionary_scaled.update(users_dump_syntheticratings05)
    synth_user_ratings_dictionary_scaled.update(users_dump_syntheticratings06)
                                                  
    with open('synthetic_ratings_new_scraper/synth_user_ratings_dictionary_scaled'+appendation+'.json', 'w') as convert_file:
        convert_file.write(json.dumps(synth_user_ratings_dictionary_scaled))
        
    synthetic01 = pd.read_pickle('synthetic_ratings_new_scraper/synthetic_ratings_01'+appendation+'.pkl')
    synthetic02 = pd.read_pickle('synthetic_ratings_new_scraper/synthetic_ratings_02'+appendation+'.pkl')
    synthetic03 = pd.read_pickle('synthetic_ratings_new_scraper/synthetic_ratings_03'+appendation+'.pkl')
    synthetic04 = pd.read_pickle('synthetic_ratings_new_scraper/synthetic_ratings_04'+appendation+'.pkl')
    synthetic05 = pd.read_pickle('synthetic_ratings_new_scraper/synthetic_ratings_05'+appendation+'.pkl')
    synthetic06 = pd.read_pickle('synthetic_ratings_new_scraper/synthetic_ratings_06'+appendation+'.pkl')
    
    synth_user_ratings_long_scaled = pd.concat([synthetic01, synthetic02, synthetic03, synthetic04, synthetic05, synthetic06], ignore_index=True)
    
    synth_user_ratings_long_scaled.to_pickle('synthetic_ratings_new_scraper/synth_user_ratings_long_scaled'+appendation+'.pkl')        

In [10]:
#make_lookup('_50')
#make_lookup('_100')
make_lookup('_250')

### Longform DF

In [7]:
def make_longform(appendation):
    synthetic01 = pd.read_pickle('synthetic_ratings_new_scraper/synthetic_ratings_01'+appendation+'.pkl')
    synthetic02 = pd.read_pickle('synthetic_ratings_new_scraper/synthetic_ratings_02'+appendation+'.pkl')
    synthetic03 = pd.read_pickle('synthetic_ratings_new_scraper/synthetic_ratings_03'+appendation+'.pkl')
    synthetic04 = pd.read_pickle('synthetic_ratings_new_scraper/synthetic_ratings_04'+appendation+'.pkl')
    synthetic05 = pd.read_pickle('synthetic_ratings_new_scraper/synthetic_ratings_05'+appendation+'.pkl')
    synthetic06 = pd.read_pickle('synthetic_ratings_new_scraper/synthetic_ratings_06'+appendation+'.pkl')
    
    synth_user_ratings_long_scaled = pd.concat([synthetic01, synthetic02, synthetic03, synthetic04, synthetic05, synthetic06], ignore_index=True)
    
    synth_user_ratings_long_scaled.to_pickle('synthetic_ratings_new_scraper/synth_user_ratings_long_scaled'+appendation+'.pkl')

In [11]:
#make_longform('_50')
#make_longform('_100')
make_longform('_250')

## Unscaled Ratings

In [8]:
with open('users_means.json') as json_file:
    user_means = json.load(json_file)

### Unscaled

In [9]:
def make_unscaled_lookup(appendation):
    # Opening JSON file
    with open('synthetic_ratings_new_scraper/users_dump_syntheticratings01'+appendation+'.json') as json_file:
        users_dump_syntheticratings01 = json.load(json_file)
    with open('synthetic_ratings_new_scraper/users_dump_syntheticratings02'+appendation+'.json') as json_file:
        users_dump_syntheticratings02 = json.load(json_file)
    with open('synthetic_ratings_new_scraper/users_dump_syntheticratings03'+appendation+'.json') as json_file:
        users_dump_syntheticratings03 = json.load(json_file)
    with open('synthetic_ratings_new_scraper/users_dump_syntheticratings04'+appendation+'.json') as json_file:
        users_dump_syntheticratings04 = json.load(json_file)
    with open('synthetic_ratings_new_scraper/users_dump_syntheticratings05'+appendation+'.json') as json_file:
        users_dump_syntheticratings05 = json.load(json_file)
    with open('synthetic_ratings_new_scraper/users_dump_syntheticratings06'+appendation+'.json') as json_file:
        users_dump_syntheticratings06 = json.load(json_file)
    
    for user in users_dump_syntheticratings01:
        user_mean = user_means[user]
        for item in users_dump_syntheticratings01[user]:
            users_dump_syntheticratings01[user][item] += user_mean  
    
    for user in users_dump_syntheticratings02:
        user_mean = user_means[user]
        for item in users_dump_syntheticratings02[user]:
            users_dump_syntheticratings02[user][item] += user_mean
    
    for user in users_dump_syntheticratings03:
        user_mean = user_means[user]
        for item in users_dump_syntheticratings03[user]:
            users_dump_syntheticratings03[user][item] += user_mean
            
    for user in users_dump_syntheticratings04:
        user_mean = user_means[user]
        for item in users_dump_syntheticratings04[user]:
            users_dump_syntheticratings04[user][item] += user_mean
            
    for user in users_dump_syntheticratings05:
        user_mean = user_means[user]
        for item in users_dump_syntheticratings05[user]:
            users_dump_syntheticratings05[user][item] += user_mean
            
    for user in users_dump_syntheticratings06:
        user_mean = user_means[user]
        for item in users_dump_syntheticratings06[user]:
            users_dump_syntheticratings06[user][item] += user_mean
            
    synth_user_ratings_dictionary_unscaled = {}
    synth_user_ratings_dictionary_unscaled.update(users_dump_syntheticratings01)
    synth_user_ratings_dictionary_unscaled.update(users_dump_syntheticratings02)
    synth_user_ratings_dictionary_unscaled.update(users_dump_syntheticratings03)
    synth_user_ratings_dictionary_unscaled.update(users_dump_syntheticratings04)
    synth_user_ratings_dictionary_unscaled.update(users_dump_syntheticratings05)
    synth_user_ratings_dictionary_unscaled.update(users_dump_syntheticratings06)
    
    with open('synthetic_ratings_new_scraper/synth_user_ratings_dictionary_unscaled'+appendation+'.json', 'w') as convert_file:
        convert_file.write(json.dumps(synth_user_ratings_dictionary_unscaled))        
        
        
    synth_user_ratings = pd.DataFrame.from_dict(users_dump_syntheticratings01).T

    synth_user_ratings.reset_index(inplace=True)
    synth_user_ratings.rename(columns={'index':'UserID'}, inplace=True)
    synth_user_ratings_long_01 = synth_user_ratings.melt(id_vars='UserID', var_name='BGGId', value_name='Rating').dropna()
    synth_user_ratings_long_01.sort_values('UserID', inplace=True)
    synth_user_ratings_long_01.reset_index(drop=True, inplace=True)

    del synth_user_ratings
    del users_dump_syntheticratings01

    gc.collect()
    
    synth_user_ratings = pd.DataFrame.from_dict(users_dump_syntheticratings02).T

    synth_user_ratings.reset_index(inplace=True)
    synth_user_ratings.rename(columns={'index':'UserID'}, inplace=True)
    synth_user_ratings_long_02 = synth_user_ratings.melt(id_vars='UserID', var_name='BGGId', value_name='Rating').dropna()
    synth_user_ratings_long_02.sort_values('UserID', inplace=True)
    synth_user_ratings_long_02.reset_index(drop=True, inplace=True)

    del synth_user_ratings
    del users_dump_syntheticratings02

    gc.collect()
    
    synth_user_ratings = pd.DataFrame.from_dict(users_dump_syntheticratings03).T

    synth_user_ratings.reset_index(inplace=True)
    synth_user_ratings.rename(columns={'index':'UserID'}, inplace=True)
    synth_user_ratings_long_03 = synth_user_ratings.melt(id_vars='UserID', var_name='BGGId', value_name='Rating').dropna()
    synth_user_ratings_long_03.sort_values('UserID', inplace=True)
    synth_user_ratings_long_03.reset_index(drop=True, inplace=True)

    del synth_user_ratings
    del users_dump_syntheticratings03

    gc.collect()
    
    synth_user_ratings = pd.DataFrame.from_dict(users_dump_syntheticratings04).T

    synth_user_ratings.reset_index(inplace=True)
    synth_user_ratings.rename(columns={'index':'UserID'}, inplace=True)
    synth_user_ratings_long_04 = synth_user_ratings.melt(id_vars='UserID', var_name='BGGId', value_name='Rating').dropna()
    synth_user_ratings_long_04.sort_values('UserID', inplace=True)
    synth_user_ratings_long_04.reset_index(drop=True, inplace=True)

    del synth_user_ratings
    del users_dump_syntheticratings04

    gc.collect()
    
    synth_user_ratings = pd.DataFrame.from_dict(users_dump_syntheticratings05).T

    synth_user_ratings.reset_index(inplace=True)
    synth_user_ratings.rename(columns={'index':'UserID'}, inplace=True)
    synth_user_ratings_long_05 = synth_user_ratings.melt(id_vars='UserID', var_name='BGGId', value_name='Rating').dropna()
    synth_user_ratings_long_05.sort_values('UserID', inplace=True)
    synth_user_ratings_long_05.reset_index(drop=True, inplace=True)

    del synth_user_ratings
    del users_dump_syntheticratings05

    gc.collect()
    
    synth_user_ratings = pd.DataFrame.from_dict(users_dump_syntheticratings06).T

    synth_user_ratings.reset_index(inplace=True)
    synth_user_ratings.rename(columns={'index':'UserID'}, inplace=True)
    synth_user_ratings_long_06 = synth_user_ratings.melt(id_vars='UserID', var_name='BGGId', value_name='Rating').dropna()
    synth_user_ratings_long_06.sort_values('UserID', inplace=True)
    synth_user_ratings_long_06.reset_index(drop=True, inplace=True)

    del synth_user_ratings
    del users_dump_syntheticratings06

    gc.collect()
    
    synth_user_ratings_long_unscaled = pd.concat([synth_user_ratings_long_01, synth_user_ratings_long_02, synth_user_ratings_long_03, synth_user_ratings_long_04, synth_user_ratings_long_05, synth_user_ratings_long_06], ignore_index=True)
    
    synth_user_ratings_long_unscaled.to_pickle('synthetic_ratings_new_scraper/synth_user_ratings_long_unscaled'+appendation+'.pkl')

In [12]:
#make_unscaled_lookup('_50')
#make_unscaled_lookup('_100')
make_unscaled_lookup('_250')

# Validate Data

In [16]:
 # Opening JSON file
with open('synthetic_ratings_new_scraper/synth_user_ratings_dictionary_unscaled_100.json') as json_file:
    synth_user_ratings_dictionary_unscaled = json.load(json_file)
    
# Opening JSON file
with open('real_ratings/real_user_ratings_dictionary_unscaled.json') as json_file:
    real_user_ratings_dictionary_unscaled = json.load(json_file)

In [17]:
# dictionary of game IDs-Names

# Load games
games = pd.read_pickle('data_cleaned_new_scraper/games.pkl')

# lists of game ids and game names
game_ids = list(games['BGGId'])
game_names = list(games['Name'])

# make lookup dictionary
game_id_lookup = {}

# store ids and names in lookup dictionary
for key, item in zip(game_ids, game_names):
    game_id_lookup[key] = item

    
del games
gc.collect()

game_id_lookup

{1: 'Die Macher',
 2: 'Dragonmaster',
 3: 'Samurai',
 4: 'Tal der Könige',
 5: 'Acquire',
 6: 'Mare Mediterraneum',
 7: 'Cathedral',
 8: 'Lords of Creation',
 9: 'El Caballero',
 10: 'Elfenland',
 11: 'Bohnanza',
 12: 'Ra',
 13: 'Catan',
 14: 'Basari',
 15: 'Cosmic Encounter',
 16: 'MarraCash',
 17: 'Button Men',
 18: 'RoboRally',
 19: 'Wacky Wacky West',
 20: 'Full Metal Planète',
 21: 'Gateway to the Stars',
 22: 'Magic Realm',
 23: 'Divine Right',
 24: 'Twilight Imperium',
 25: 'Battlemist',
 26: 'Age of Renaissance',
 27: 'Supremacy: The Game of the Superpowers',
 28: 'Illuminati',
 29: 'Terrain Vague',
 30: 'Dark Tower',
 31: 'Dark World',
 32: 'Buffalo Chess',
 34: 'Arkham Horror',
 36: 'Federation & Empire',
 37: 'Dragon Masters',
 38: 'Runes',
 39: 'Darkover',
 40: 'Borderlands',
 41: "Can't Stop",
 42: 'Tigris & Euphrates',
 43: 'Airlines',
 44: 'David & Goliath',
 45: 'Perudo',
 46: 'Medici',
 47: 'Chinatown',
 48: 'Krieg und Frieden',
 49: 'Mamma Mia!',
 50: 'Lost Cities',
 

In [18]:
user='zusterdoor'

In [19]:
this_user = pd.DataFrame(real_user_ratings_dictionary_unscaled[user].values(), index=real_user_ratings_dictionary_unscaled[user].keys())
this_user.reset_index(inplace=True)
this_user['Game'] = this_user['index'].astype('int32').map(game_id_lookup)
x4 = this_user.sort_values([0, 'index'], ascending=False)

In [20]:
x4.sort_values(0, ascending=False)

index    0                Game
4    278  9.5     Catan Card Game
0  21763  9.0            Mr. Jack
2     13  8.0               Catan
3     50  7.5         Lost Cities
1    132  6.0  Caesar & Cleopatra

In [21]:
this_user = pd.DataFrame(synth_user_ratings_dictionary_unscaled[user].values(), index=synth_user_ratings_dictionary_unscaled[user].keys())
this_user.reset_index(inplace=True)
this_user['Game'] = this_user['index'].astype('int32').map(game_id_lookup)
x3 = this_user.sort_values([0, 'index'], ascending=False)

In [22]:
x3.sort_values(0, ascending=False).head(30)

index         0                                               Game
4      278  9.500000                                    Catan Card Game
6   203219  9.350000                           Rivals for Catan: Deluxe
15   22766  9.309530  Die Siedler von Catan: Das Kartenspiel – 10th ...
17   27802  9.305202                         Anno 1701: Das Kartenspiel
44   91534  9.174144                                 Struggle for Catan
53    2338  9.163267                                     Starship Catan
58  151016  9.158695                                   Provincia Romana
73  188866  9.135679                                     Awkward Guests
74   33962  9.135103                                Match of the Season
77    5549  9.103900                              Das Wasser des Lebens
79   66056  9.098047                                   Rivals for Catan
85   56246  9.086998                                            Goblins
95  135877  9.067756                                          Fish Cook
0    21763  9.000000                                           Mr. Jack
7   145645  8.900000                              Le Fantôme de l'Opéra
25   55427  8.810000                               Mr. Jack in New York
75  170624  8.747967                        Crusaders: Thy Will Be Done
78  234314  8.732108                                             Dôjima
80  229218  8.000000  A Game of Thrones: Catan – Brotherhood of the ...
2       13  8.000000                                              Catan
67  147240  8.000000                              Catan: Family Edition
76  117985  8.000000                                   Star Trek: Catan
70  298278  8.000000                  Catan: 25 Jahre Jubiläums-Edition
24  305668  8.000000                    Catan: 25th Anniversary Edition
5   338697  8.000000                                  CATAN: 3D Edition
83    6778  8.000000                          The Settlers of Zarahemla
99  341416  7.645139                                         High Score
96  266083  7.644206                                         L.L.A.M.A.
94   29489  7.642344                                      Tai Chi Chuan
93    2369  7.641640                                             Fiasko

# Build User Means Dictionary

In [4]:
def get_user_means(path_item):

    temp_dictionary = {}
    
    path = 'data_cleaned/ratings_matrix_cleaned_'+path_item+'.pkl'
    user_matrix = pd.read_pickle(path)
    user_matrix = user_matrix.T
    user_matrix.index = user_matrix.index.astype('int32')
    user_matrix.shape
    
    print('Processing '+str(path_item))
    for user in user_matrix.columns:
        
        # get the mean rating for that user
        user_mean = user_matrix[user].mean()
        
        user_means[user] = user_mean

In [5]:
user_means = {}

get_user_means('01')
get_user_means('02')
get_user_means('03')
get_user_means('04')
get_user_means('05')
get_user_means('06')

Processing 01
Processing 02
Processing 03
Processing 04
Processing 05
Processing 06


In [6]:
user_means['Threnody']

7.222485207100592

In [7]:
with open('users_means.json', 'w') as convert_file:
     convert_file.write(json.dumps(user_means))

In [8]:
user_means = pd.DataFrame.from_dict(user_means, columns=['user_mean'], orient='index')

In [9]:
user_means.to_pickle('user_means.pkl')

In [ ]:
with open('users_means.json') as json_file:
    user_means = json.load(json_file)